In [1]:
import torch
import torch.nn as nn
import numpy as np
import tqdm
from sklearn.metrics import roc_auc_score
from torch.utils.data import DataLoader
from dataset.movielens import MovieLens1MDataset, MovieLens20MDataset

In [2]:
def get_dataset(name, path):
    if name == 'movielens1M':
        return MovieLens1MDataset(path)
    elif name == 'movielens20M':
        return MovieLens20MDataset(path)
    else:
        raise ValueError('unknown dataset name: ' + name)

In [3]:
dataset = get_dataset("movielens1M", "../DataSets/ncf/ratings.dat")

In [4]:
train_length = int(len(dataset) * 0.2)
valid_length = int(len(dataset) * 0.1)
test_length = len(dataset) - train_length - valid_length
train_dataset, valid_dataset, test_dataset = torch.utils.data.random_split(dataset, (train_length, valid_length, test_length))

In [5]:
train_data_loader = DataLoader(train_dataset, batch_size=4)
valid_data_loader = DataLoader(valid_dataset, batch_size=4)
test_data_loader = DataLoader(test_dataset, batch_size=4)

In [6]:
class FieldAwareFactorizationMachineModel(nn.Module):

    def __init__(self, field_dims, embed_dim):
        super(FieldAwareFactorizationMachineModel, self).__init__()
        self.linear = FeaturesLinear(field_dims)
        self.ffm = FieldAwareFactorizationMachine(field_dims, embed_dim)

    def forward(self, x):
        ffm_term = torch.sum(torch.sum(self.ffm(x), dim=1), dim=1, keepdim=True)
        # 其中线性部分是w0+sum(wi*xi), ffm部分是sum(sum((vi,f*vj,f)*xi*xj))
        x = self.linear(x) + ffm_term
        return torch.sigmoid(x.squeeze(1))

In [7]:
class FeaturesLinear(nn.Module):

    def __init__(self, field_dims, output_dim=1):
        super(FeaturesLinear, self).__init__()
        self.fc = nn.Embedding(sum(field_dims), output_dim)
        self.bias = nn.Parameter(torch.zeros((output_dim,)))
        self.offsets = np.array((0, *np.cumsum(field_dims)[:-1]), dtype=np.long)

    def forward(self, x):
        print("FeaturesLinear x=", x)
        print(self.offsets)
        print("FeaturesLinear x=", x.new_tensor(self.offsets, dtype=np.long))
        print("----------------------")
        x = x + x.new_tensor(self.offsets, dtype=np.long).unsqueeze(0)
        print("FeaturesLinear return=", torch.sum(self.fc(x), dim=1) + self.bias)
        return torch.sum(self.fc(x), dim=1) + self.bias

In [8]:
class FieldAwareFactorizationMachine(nn.Module):

    def __init__(self, field_dims, embed_dim):
        super(FieldAwareFactorizationMachine, self).__init__()
        self.num_fields = len(field_dims)
        self.embeddings = nn.ModuleList([
            nn.Embedding(sum(field_dims), embed_dim) for _ in range(self.num_fields)
        ])
        self.offsets = np.array((0, *np.cumsum(field_dims)[:-1]), dtype=np.long)
        for embedding in self.embeddings:
            nn.init.xavier_normal_(embedding.weight.data)

    def forward(self, x):

        x = x + x.new_tensor(self.offsets, dtype=np.long).unsqueeze(0)
        xs = [self.embeddings[i](x) for i in range(self.num_fields)]
        ix = list()
        for i in range(self.num_fields - 1):
            for j in range(i + 1, self.num_fields):
                ix.append(xs[j][:, i] * xs[i][:, j])
        ix = torch.stack(ix, dim=1)
        return ix

In [9]:
model = FieldAwareFactorizationMachineModel(dataset.field_dims, embed_dim=4)

In [10]:
dataset.field_dims

array([6040, 3952])

In [11]:
criterion = torch.nn.BCELoss()
optimizer = torch.optim.Adam(params=model.parameters(), lr=0.001, weight_decay=1e-6)

In [12]:
def train(model, optimizer, data_loader, criterion, device, log_interval=100):
    model.train()
    total_loss = 0
    tk0 = tqdm.tqdm(data_loader, smoothing=0, mininterval=1.0)
    for i, (fields, target) in enumerate(tk0):
        fields, target = fields.to(device), target.to(device)
        y = model(fields)
        loss = criterion(y, target.float())
        model.zero_grad()
        loss.backward()
        optimizer.step()
        total_loss += loss.item()
        if (i + 1) % log_interval == 0:
            tk0.set_postfix(loss=total_loss / log_interval)
            total_loss = 0

In [ ]:
for epoch_i in range(2):
    train(model, optimizer, train_data_loader, criterion, "cpu")

  0%|          | 0/50011 [00:00<?, ?it/s]

FeaturesLinear x= tensor([[2662, 1611],
        [1912, 1199],
        [1670,   57],
        [4823, 1213]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 0.5002],
        [ 1.0825],
        [-1.3058],
        [ 0.5944]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[1508, 3750],
        [1122,  382],
        [1305,  484],
        [ 147,  363]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-0.7869],
        [-0.3828],
        [-1.8224],
        [ 1.1183]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[ 301,  179],
        [ 529, 1290],
        [5568, 2790],
        [5768, 1499]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-1.5850],
        [-0.4052],
        [-2.2628],
        [ 2.7107]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[2

  0%|          | 12/50011 [00:01<1:11:10, 11.71it/s]

FeaturesLinear x= tensor([[3510, 3526],
        [4091, 2173],
        [2105, 2398],
        [2191, 2368]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-1.4541],
        [ 1.6030],
        [-0.9517],
        [-0.8798]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4429, 3104],
        [4679,  952],
        [2556, 2057],
        [3970, 2639]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-1.3389],
        [-0.2752],
        [-2.1971],
        [ 1.8363]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[ 301, 3285],
        [3823, 3711],
        [4955, 2925],
        [5557, 2101]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-1.6952],
        [-0.2492],
        [ 1.4738],
        [ 1.0874]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[1

  0%|          | 26/50011 [00:02<1:05:43, 12.68it/s]

...

 48%|████▊     | 24157/50011 [17:49<19:04, 22.59it/s, loss=0.655]

FeaturesLinear x= tensor([[4276, 2351],
        [2961, 2796],
        [4980,  317],
        [3575, 2814]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 1.7382],
        [ 0.8623],
        [ 2.8723],
        [-3.5045]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4657, 2159],
        [3379, 3826],
        [5823, 1026],
        [1049, 1731]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[-1.3406],
        [-0.1665],
        [-0.2023],
        [-0.7502]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4887,  902],
        [5424, 1192],
        [3549, 2711],
        [   7,  505]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[1.1072],
        [0.5604],
        [0.8153],
        [0.3646]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4684,

        [3649, 1232]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 0.1431],
        [-0.7396],
        [ 0.6524],
        [ 2.0353]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[ 423, 1891],
        [2913, 3724],
        [3223, 2592],
        [3229, 1213]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[0.7946],
        [0.0903],
        [0.3957],
        [1.5733]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[5644,   28],
        [4478, 2193],
        [5981, 2639],
        [3310,   59]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 1.0220],
        [ 0.2410],
        [ 1.2840],
        [-1.0085]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4061, 2857],
        [4237, 1731],
        [5538, 2582],
        [2667, 3910]], dtype=tor

FeaturesLinear return= tensor([[ 0.0086],
        [-0.5688],
        [ 1.9054],
        [ 0.2059]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[4447, 1213],
        [5663, 1626],
        [ 428, 2699],
        [1646, 2497]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 2.8184],
        [ 0.7758],
        [ 0.5054],
        [-0.6166]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[3587, 2950],
        [2001, 3447],
        [3099, 3175],
        [ 845, 3862]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 1.5827],
        [ 0.4527],
        [-0.4917],
        [ 0.2269]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[1297, 1209],
        [3952, 1239],
        [3415, 2456],
        [2821,  214]], dtype=torch.int32)
tensor([[ 1.4913],
        [-0.4587],
        [-0.0661],
        [-0.2166]], grad_fn=<AddBackward0>)
F

        [3402, 2996]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 0.5966],
        [-0.3611],
        [ 0.9388],
        [ 0.1651]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[1644, 2917],
        [ 875, 1274],
        [4344,  908],
        [ 532, 2996]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 1.4023],
        [-0.3354],
        [-0.6164],
        [ 0.5703]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[ 730, 2833],
        [5282, 2548],
        [3836, 2370],
        [5735, 1222]], dtype=torch.int32)
[   0 6040]
FeaturesLinear x= tensor([   0, 6040])
----------------------
FeaturesLinear return= tensor([[ 0.4634],
        [-0.6895],
        [ 0.5062],
        [ 0.6469]], grad_fn=<AddBackward0>)
FeaturesLinear x= tensor([[1666,  759],
        [1794,  379],
        [5403, 2960],
        [1263, 2605]], dtype